# TP 2-3 : Branch-and-bound applied to a knapsack problem

### Initialisation (à faire une seule fois)

In [8]:
import Pkg; 
Pkg.add("GraphRecipes");
Pkg.add("Plots"); 
using GraphRecipes, Plots #only used to visualize the search tree at the end of the branch-and-bound

   Resolving package versions...
  No Changes to `~/.julia/environments/v1.6/Project.toml`
  No Changes to `~/.julia/environments/v1.6/Manifest.toml`
Precompiling project...
  ✓ TestOptinum
  1 dependency successfully precompiled in 4 seconds (270 already precompiled)
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.6/Project.toml`
  No Changes to `~/.julia/environments/v1.6/Manifest.toml`
Precompiling project...
  ✓ TestOptinum
  1 dependency successfully precompiled in 3 seconds (270 already precompiled)


### Récupération des données

In [ ]:
"""Open and read a KnapFile.

Args:
    filename (String): the name of the file to read.

Returns:
    price (Vector{Int64}): prices of items to put in the KnapSack.
    weight (Vector{Int64}): weights of items to put in the KnapSack.
    capacity (Int64): the maximum capacity of the KnapSack.

"""
function readKnapInstance(filename)
    price=[]
    weight=[]
    capacity = -1
    open(filename) do f
        for i in 1:3
            tok = split(readline(f))
            if (tok[1] == "ListPrices=")
                for i in 2:(length(tok)-1)
                    push!(price,parse(Int64, tok[i]))
                end
            elseif (tok[1] == "ListWeights=")
                for i in 2:(length(tok)-1)
                    push!(weight,parse(Int64, tok[i]))
                end
            elseif (tok[1] == "Capacity=")
                capacity = parse(Int64, tok[2])
            else
                println("Unknown read :", tok)
            end 
        end
    end
    return price, weight, capacity
end

In [26]:
# on teste de lire tous les fichiers .opb
for (root, dirs, files) in walkdir("data")
    for file in files
        if endswith(file, ".opb")
            readKnapInstance(root * "/" * file)
        end
    end
end

### Procédure d'application des tests de sondabilités TA, TO et TR pour le cas de la relaxation linéaire

In [ ]:
function TestsSondabilite_relaxlin(x, price, weight, capacity, BestProfit, Bestsol, affich)
    TA, TO, TR = false, false, false
    if (!Constraints(x, weight, capacity)) # Test de faisabilite
        TA = true
        if affich
            println("TA")
        end
    elseif (Objective(x, price) <= BestProfit) # Test d'optimalite
        TO = true
        if affich
            println("TO")
        end
    elseif (AllDef(x)) # Test de resolution
        TR = true
        if affich
            println("TR : solution ", " de profit ", Objective(x, price))
        end
        if (Objective(x, price) >= BestProfit) # Le profit de la solution trouvée est meilleur que les autres
            if affich
                println("\t-> Cette solution a un meilleur profit.")
            end
            # On remplace la solution et le profit par les nouvelles valeurs
            Bestsol = x
            BestProfit = Objective(x, price)
        else
            if affich
                println("\t-> Cette solution est moins bonne.")
            end
        end
    else
        if affich 
            println("non sondable")
        end
    end
    if affich
        println("\n")
    end
    
    TA, TO, TR, Bestsol, BestProfit
end

### Procédure de séparation et stratégie d'exploration permettant de se placer au prochain noeud à traiter

In [ ]:
function SeparerNoeud_relaxlin(price, listvars, listvals)
    # Le noeud est non-sondable. Appliquer le critère de séparation pour le séparer en sous-noeuds 

    # Cas du noeud le plus à gauche

    # On sépare le noeud actuel en 2 sous-noeuds
    predX = pop!(listvars)
    nextX0 = copy(predX)
    nextX1 = copy(predX)

    # On initialise leurs valeurs à zéro
    val0 = 0
    val1 = 0

    # On fixe la nouvelle variable des deux sous-noeuds
    n = length(predX)
    for i in 1:n
        if predX[i] == -1
            # L'un a zéro
            nextX0[i] = 0
            # L'autre a un
            nextX1[i] = 1

            # On calcule leurs valeurs
            val0 = Objective(nextX0, price)
            val1 = Objective(nextX1, price)
            break
        end
    end
    
    # On ajoute les sous-noeuds a la pile des noeuds a explorer
    push!(listvars, nextX0)
    push!(listvars, nextX1)

    # On ajoute aussi leurs valeurs
    push!(listvals, val0)
    push!(listvals, val1)

    listvars, listvals
end


function ExplorerAutreNoeud_relaxlin(listvars, listvals)
    # Le noeud est sondable, on l'enlève de la pile des noeuds à sonder
    
    stop = false
    if (length(listvars) > 1)
        # On passe au noeud suivant
        var = pop!(listvars)
        val = pop!(listvals)
    else
        # Il n'y a pas d'autre noeud
        println("\nFINISHED")
        stop = true
    end

    listvars, listvals, stop 
end

In [ ]:
# Fonction objectif que l'on souhaite maximiser/minimiser (évalué dans le meilleur des cas)
Objective(x, price) = 
    sum(
        if x[i] < 0
            price[i]
        else
            price[i]*x[i] 
        end
            for i in 1:length(x)
    )

# Fonction permettant de vérfier toutes les contraintes du modèle (dans le meilleur des cas)
Constraints(x, weight, capacity) =
    sum(
        if x[i] < 0
            0
        else 
            weight[i]*x[i]
        end
            for i in 1:length(x)
    ) <= capacity

# Fonction qui nous dis si toutes les variables de x sont fixées
function AllDef(x)
    for i in 1:length(x)
        if x[i] < 0
            return false
        end
    end
    return true
end

In [ ]:
function SolveKnapInstance(filename)

    # Extraction des données
    price, weight, capacity = readKnapInstance(filename)

    println("Capacity : ", capacity, " | Number of objects : ", length(price), "\n")

    # Pour dessiner le graph
    trParentnodes = Int64[]
    trChildnodes = Int64[]
    trNamenodes = []

    # Liste des variable pour naviguer de noeuds en noeuds
    listvars = []
    listvals = []
    listnodes = []

    # La meilleur solution et sa valeur
    BestProfit = -1
    Bestsol = []

    # Compter le nombre de noeud explorés
    current_node_number = 0

    stop = false
    affich = false

    # On ajoute le premier noeud à explorer (la racine)
    push!(listvars, [-1 for p in price])
    push!(listvals, Objective(last(listvars), price))
    push!(listnodes, 1)
    push!(trNamenodes, 0)
    newnodeid = 2

    while (!stop)

        # Le noeud actuel
        x = last(listvars)

        if affich
            print("----------\nNode n°", current_node_number, " : ")
            println(" ")
            println("\nPrevious Solution memorized ", " with bestprofit ", BestProfit, "\n")
        end

        # Test de sondabilité du noeud actuel
        #   -> On mets a jour la solution et sa valeur si besoin
        TA, TO, TR, Bestsol, BestProfit = TestsSondabilite_relaxlin(x, price, weight, capacity, BestProfit, Bestsol, affich)
        
        is_node_sondable = TA || TO || TR
        if (!is_node_sondable)
            # Le noeud n'est pas sondable, on le sépare en 2 sous-noeuds
            listvars, listvals = SeparerNoeud_relaxlin(price, listvars, listvals)

            curnode = pop!(listnodes)

            push!(trParentnodes, curnode)
            push!(trParentnodes, curnode)

            push!(listnodes, newnodeid+1)
            push!(listnodes, newnodeid)

            push!(trChildnodes, newnodeid)
            push!(trChildnodes, newnodeid+1)

            push!(trNamenodes, newnodeid-1)
            push!(trNamenodes, newnodeid)

            newnodeid += 2

        else
            # Le noeud est sondable, on passe au noeud suivant
            listvars, listvals, stop = ExplorerAutreNoeud_relaxlin(listvars, listvals)

            pop!(listnodes)
        end

        # On évite de spammer l'output donc  on n'affiche pas tout les résultats
        if current_node_number % 1000000 == 100
            affich = true
        else
            affich = false
        end

        current_node_number += 1
    end

    println("\n******\n\nOptimal value = ", BestProfit, "\n\nOptimal x = ", Bestsol)

    trParentnodes, trChildnodes, trNamenodes
end

In [ ]:
trParentnodes, trChildnodes, trNamenodes = SolveKnapInstance("data/circle/knapPI_16_8_1000_1_-2291.opb")
graphplot(trParentnodes, trChildnodes, names=trNamenodes, method=:tree)